In [1]:
import pandas as pd
import torch as t
from pathlib import Path
from transformers import AutoTokenizer,AutoModel, GPTNeoXForCausalLM
from tqdm.auto import tqdm
import numpy as np
from pandarallel import pandarallel
import os

pandarallel.initialize(nb_workers=16,progress_bar=True)

INFO: Pandarallel will run on 16 workers.
INFO: Pandarallel will use standard multiprocessing data transfer (pipe) to transfer data between the main process and workers.


In [2]:
pile_df = pd.read_json("data/pile_samples.jsonl",lines=True)
pile_df.head()

text  \
0  ---\naddress: '$^{1}$ Department of Computer E...   
1  ---\nabstract: 'We prove that the law of a ran...   
2  ---\nabstract: 'A nonperturbative numerical ev...   
3  ---\nabstract: 'Vacancy-induced magnetization ...   
4  ---\nauthor:\n- |\n    Robert G. Endres$^{1,2}...   

                         meta pile_set_name  
0  {'pile_set_name': 'ArXiv'}         ArXiv  
1  {'pile_set_name': 'ArXiv'}         ArXiv  
2  {'pile_set_name': 'ArXiv'}         ArXiv  
3  {'pile_set_name': 'ArXiv'}         ArXiv  
4  {'pile_set_name': 'ArXiv'}         ArXiv

In [3]:
device = t.device("cuda" if t.cuda.is_available() else "mps")

In [4]:
MODEL_NAME = "EleutherAI/pythia-70m-deduped"

In [5]:
tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)

## Load The Pile

In [6]:
dfs = [pd.read_parquet(f"data/mem/memorization_70m-deduped-v0_143000_rank{rank}.parquet") for rank in range(4)]
df = pd.concat(dfs, ignore_index=True)

In [7]:
df["decoded_context"] = df.apply(lambda x: tokenizer.decode(x["context"]),axis=1)
df["decoded_generation"] = df.apply(lambda x: tokenizer.decode(x["generation"]),axis=1)
df["decoded_true_continuation"] = df.apply(lambda x: tokenizer.decode(x["true_continuation"]),axis=1)

In [42]:
# Sweep over different numbers of matching tokens
max_tokens_to_check = 32  # Maximum number of tokens to check for matching
results = []

for n in range(0, max_tokens_to_check + 1):    
    # all(row['generation'][:n] == row['true_continuation'][:n]) and 
    n_token_match = df.apply(
        lambda row:((n == max_tokens_to_check) or (row['generation'][n] != row['true_continuation'][n])) and
                   (n == 0 or sum(g != t for g, t in zip(row['generation'][:n], row['true_continuation'][:n])) == 1),
        axis=1
    )
    
    # Count matches and calculate percentage
    matching_count = n_token_match.sum()
    matching_percentage = matching_count / len(df) * 100    
    results.append((df[n_token_match], matching_count, matching_percentage))
    print(f"First {n} tokens match with 1 differing token: {matching_count} samples ({matching_percentage:.2f}%)")

First 0 tokens match with 1 differing token: 5784 samples (28.59%)
First 1 tokens match with 1 differing token: 4726 samples (23.36%)
First 2 tokens match with 1 differing token: 777 samples (3.84%)
First 3 tokens match with 1 differing token: 749 samples (3.70%)
First 4 tokens match with 1 differing token: 726 samples (3.59%)
First 5 tokens match with 1 differing token: 670 samples (3.31%)
First 6 tokens match with 1 differing token: 712 samples (3.52%)
First 7 tokens match with 1 differing token: 779 samples (3.85%)
First 8 tokens match with 1 differing token: 1106 samples (5.47%)
First 9 tokens match with 1 differing token: 742 samples (3.67%)
First 10 tokens match with 1 differing token: 570 samples (2.82%)
First 11 tokens match with 1 differing token: 223 samples (1.10%)
First 12 tokens match with 1 differing token: 190 samples (0.94%)
First 13 tokens match with 1 differing token: 179 samples (0.88%)
First 14 tokens match with 1 differing token: 213 samples (1.05%)
First 15 tokens

In [43]:
num_matching_tokens = 10
explore_df = results[num_matching_tokens][0]

In [44]:
explore_df['decoded_context'].values

array([' (630 nm and 700 nm) used for LLLT \\[[@B16-brainsci-09-00179]\\] to investigate the mechanisms underlying neuromodulation \\[[@',
       'nodes}} \\sum _{i=1}^{N_\\mathrm{nodes}} |\\varvec{x}_i(\\varvec{q}) - \\varvec',
       '\n                                    {\n                                        "type": "NamedArgument",\n                                        "name": {\n                                            "type": "',
       '$ $\\mathsf{\\mu}$m. Moreover, the thickness of the dielectric spacer is obtained from Equation ([13](#FD13-nanomaterials-09-01351',
       '_title">Voir le journal d\\\'installation</string>\n  <string name="menu_delete_title">Tout supprimer</',
       ' was a delete marker.\r\n         */\r\n        public boolean isDeleteMarker() {\r\n            return deleteMarker;\r\n        }\r\n\r\n        public void setDelete',
       '. Let b = 211115 - 211112. Factor -63/5*f**2 - 72/5*f - 12/5 - b',
       ' (1996); State v. Rouse, 339 N.C.

In [45]:
explore_df[['decoded_generation','decoded_true_continuation',"acc"]].values

array([['B17-brainsci-09-00179]\\].\n\nThe results of the present study showed that the LLLT-induced neuromodulation was significantly increased',
        'B1-brainsci-09-00179]\\]. Here, the primary aim is to better understand the extent of optically induced tissue heating (primarily due to water',
        0.28125],
       ['{x}_i(\\varvec{q})| \\leq \\sum _{i=1}^{N_\\mathrm{nodes}} |\\varvec{x}_',
        '{x}_i(\\varvec{q}_f) |. \\end{aligned}$$\\end{document}$$The kinematic variable error is defined as the mean',
        0.28125],
       ['String",\n                                            "name": {\n                                                "type": "String",\n                                                "name": {\n                                                "type',
        'Identifier",\n                                            "name": "y"\n                                        },\n                                        "value": {\n                           

In [7]:
df_perfect = df[df['acc'] == 1]

In [10]:
df_nonmem = df[df['acc'] == 0]
df_nonmem['decoded_full'] = tokenizer.batch_decode(df_nonmem.apply(lambda x: list(x['context']) + list(x['true_continuation']),axis=1))

/var/folders/wj/q3w38sf543xc8fy9rx8yqzrh0000gn/T/ipykernel_83555/3429006096.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_nonmem['decoded_full'] = tokenizer.batch_decode(df_nonmem.apply(lambda x: list(x['context']) + list(x['true_continuation']),axis=1))


In [11]:
df_nonmem.head(32)

acc                                            context  \
0   0.0  [8148, 412, 29628, 653, 264, 6420, 275, 617, 1...   
1   0.0  [72, 5, 310, 370, 36, 63, 18, 5, 6032, 2822, 8...   
2   0.0  [1509, 15, 2896, 436, 1127, 13, 3668, 273, 146...   
3   0.0  [187, 6217, 5543, 39, 10948, 947, 1703, 428, 3...   
4   0.0  [776, 6264, 285, 9787, 16027, 497, 387, 512, 2...   
5   0.0  [288, 3560, 407, 5141, 970, 30267, 42, 15, 380...   
6   0.0  [187, 187, 4125, 2207, 67, 2823, 310, 2970, 76...   
7   0.0  [187, 187, 33651, 368, 281, 10078, 275, 39858,...   
8   0.0  [1677, 323, 247, 642, 14, 21272, 390, 642, 14,...   
9   0.0  [1361, 747, 1363, 24171, 253, 1943, 4715, 6970...   
10  0.0  [253, 44016, 17976, 285, 9447, 5766, 1632, 273...   
11  0.0  [187, 50274, 27, 278, 64, 2577, 20226, 9, 3220...   
12  0.0  [1218, 699, 84, 715, 8668, 15, 187, 187, 2513,...   
13  0.0  [839, 1673, 669, 1906, 64, 17, 41, 64, 90, 30,...   
14  0.0  [17401, 13, 1077, 14, 676, 14, 15177, 1941, 15...   
15  0.0  [3127, 13, 4240, 187, 93, 187, 93, 187, 93, 18...   
16  0.0  [2701, 313, 74, 15, 70, 15, 575, 47787, 370, 8...   
17  0.0  [13993, 5481, 2746, 310, 17903, 347, 187, 187,...   
18  0.0  [64, 14337, 64, 4065, 426, 1881, 15, 42316, 64...   
19  0.0  [387, 1390, 13, 611, 3090, 1559, 67, 2381, 777...   
20  0.0  [18654, 275, 285, 22061, 2325, 91, 343, 3612, ...   
21  0.0  [3713, 437, 1009, 9513, 342, 370, 66, 64, 18, ...   
22  0.0  [19502, 10620, 342, 14561, 1005, 273, 253, 990...   
23  0.0  [4951, 12594, 13, 14782, 731, 15, 187, 187, 19...   
24  0.0  [4888, 187, 4, 3709, 654, 14877, 15, 73, 31, 1...   
25  0.0  [14270, 275, 247, 12246, 281, 3657, 747, 46733...   
26  0.0  [1160, 16072, 342, 247, 1180, 273, 439, 338, 5...   
27  0.0  [4241, 551, 370, 4414, 28541, 8207, 28288, 428...   
28  0.0  [9239, 10054, 323, 581, 15, 49321, 15, 1292, 3...   
29  0.0  [367, 571, 88, 2284, 3723, 32410, 4033, 255, 9...   
30  0.0  [14059, 10, 9665, 6421, 61, 1378, 3577, 282, 3...   
31  0.0  [4496, 2028, 479, 849, 4555, 436, 1214, 8893, ...   

                                           generation  \
0   [187, 187, 510, 5101, 369, 28115, 13, 253, 510...   
1   [393, 2981, 10952, 359, 452, 1764, 2043, 92, 2...   
2   [644, 3863, 15, 187, 187, 510, 1895, 369, 326,...   
3   [760, 2181, 359, 476, 513, 310, 281, 755, 253,...   
4   [253, 1387, 273, 1146, 247, 346, 33979, 3128, ...   
5   [9122, 3788, 1712, 1704, 20, 5256, 20, 14, 113...   
6   [310, 2970, 767, 41196, 898, 37048, 323, 1679,...   
7   [403, 417, 2908, 275, 253, 4803, 15, 187, 187,...   
8   [253, 1971, 273, 19798, 5988, 2923, 15, 187, 1...   
9   [31100, 323, 253, 1971, 273, 10397, 13, 9454, ...   
10  [253, 14511, 13, 253, 1894, 273, 253, 39092, 3...   
11  [966, 326, 17930, 253, 5673, 187, 605, 187, 60...   
12  [247, 1805, 685, 253, 643, 15, 187, 187, 510, ...   
13  [941, 13, 359, 897, 253, 1072, 941, 347, 275, ...   
14  [535, 50276, 11, 1785, 27167, 318, 818, 27506,...   
15  [187, 187, 42, 1353, 247, 2372, 13477, 670, 25...   
16  [1180, 370, 47, 5, 273, 253, 370, 76, 2911, 39...   
17  [14, 10722, 14299, 6046, 310, 908, 13, 253, 59...   
18  [2554, 1067, 3401, 187, 50270, 1286, 15, 34046...   
19  [62, 309, 1353, 417, 2119, 309, 476, 923, 253,...   
20  [34, 976, 275, 1784, 611, 17685, 304, 1947, 17...   
21  [323, 512, 370, 51, 61, 249, 61, 1588, 92, 34,...   
22  [14561, 3237, 15, 844, 671, 2319, 253, 14940, ...   
23  [497, 47214, 15, 187, 187, 510, 806, 7497, 497...   
24  [4, 3709, 654, 43930, 15, 73, 31, 190, 187, 4,...   
25  [17959, 5680, 556, 644, 247, 2201, 5691, 323, ...   
26  [637, 285, 753, 13, 346, 42, 1353, 7016, 13, 5...   
27  [4, 187, 50254, 4, 187, 50254, 4, 187, 50254, ...   
28  [13, 309, 476, 626, 1014, 755, 247, 28725, 15,...   
29  [1381, 346, 41, 2350, 995, 346, 41, 2350, 1381...   
30  [5, 310, 253, 3943, 2622, 4972, 281, 253, 3943...   
31  [1611, 281, 897, 352, 13, 352, 2722, 253, 2715...   

                                    true_continuation  idx  \
0   [7160, 69

In [8]:
df_perfect['decoded_full'] = tokenizer.batch_decode(df_perfect.apply(lambda x: list(x['context']) + list(x['true_continuation']),axis=1))

/var/folders/wj/q3w38sf543xc8fy9rx8yqzrh0000gn/T/ipykernel_83555/2412182024.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_perfect['decoded_full'] = tokenizer.batch_decode(df_perfect.apply(lambda x: list(x['context']) + list(x['true_continuation']),axis=1))


In [9]:
df_perfect.head(32)

acc                                            context  \
3795  1.0  [5584, 4196, 1228, 187, 1036, 4, 209, 21723, 2...   
3796  1.0  [50262, 61, 2099, 92, 8861, 94, 187, 50262, 61...   
3797  1.0  [475, 50272, 953, 24781, 778, 320, 908, 281, 1...   
3798  1.0  [424, 380, 16101, 313, 433, 17889, 3104, 10, 2...   
3799  1.0  [3498, 2262, 2369, 40, 736, 13, 3956, 27, 21, ...   
3800  1.0  [187, 187, 4, 21737, 281, 253, 14325, 9107, 68...   
3801  1.0  [66, 15, 3122, 187, 475, 8283, 313, 68, 10, 88...   
3802  1.0  [8161, 13, 2975, 15, 10701, 285, 3915, 9308, 3...   
3803  1.0  [94, 187, 50262, 61, 2043, 92, 3306, 2138, 138...   
3804  1.0  [43518, 66, 1619, 66, 43518, 66, 1619, 66, 435...   
3805  1.0  [187, 50274, 60, 18, 62, 470, 187, 50274, 60, ...   
3806  1.0  [43518, 66, 1619, 66, 43518, 66, 1619, 66, 435...   
3807  1.0  [1010, 558, 187, 50270, 8428, 3145, 60, 1010, ...   
3808  1.0  [1314, 11294, 285, 4974, 32314, 7855, 32705, 6...   
3809  1.0  [3306, 724, 34, 1035, 1637, 47562, 423, 92, 33...   
3810  1.0  [18030, 17466, 27, 470, 187, 50276, 78, 64, 25...   
3811  1.0  [35, 14024, 2407, 92, 86, 16052, 2690, 92, 76,...   
3812  1.0  [50276, 12852, 15, 2490, 50276, 7749, 15, 2490...   
3813  1.0  [1019, 8402, 94, 187, 50262, 61, 2099, 92, 879...   
3814  1.0  [1019, 8402, 94, 187, 50262, 61, 2099, 92, 879...   
3815  1.0  [6877, 36694, 3481, 378, 31219, 2277, 49412, 3...   
3816  1.0  [6740, 568, 19203, 15, 4305, 6750, 3866, 31, 1...   
3817  1.0  [17260, 15, 2949, 7651, 30609, 32221, 3003, 18...   
3818  1.0  [94, 187, 50262, 61, 2043, 92, 3306, 2138, 79,...   
3819  1.0  [625, 35922, 685, 368, 871, 752, 281, 513, 342...   
3820  1.0  [61, 2099, 92, 8828, 94, 187, 50262, 61, 2099,...   
3821  1.0  [50274, 565, 11061, 64, 1088, 28, 535, 50274, ...   
3822  1.0  [50270, 740, 187, 50271, 22000, 50270, 740, 18...   
3823  1.0  [29520, 35491, 1677, 4454, 187, 1413, 27, 4316...   
3824  1.0  [2490, 50276, 32942, 15, 2490, 50276, 32296, 1...   
3825  1.0  [73, 18, 2730, 1288, 31, 2379, 50276, 29, 73, ...   
3826  1.0  [966, 568, 34856, 66, 19, 3, 2654, 568, 26919,...   

                                             generation  \
3795  [783, 346, 17736, 3287, 187, 4, 368, 778, 417,...   
3796  [669, 8604, 60, 805, 431, 1019, 8402, 94, 187,...   
3797  [4110, 33278, 9149, 3003, 28827, 43227, 4889, ...   
3798  [50262, 61, 2099, 92, 8860, 94, 2490, 50262, 6...   
3799  [69, 7675, 27, 2369, 40, 736, 13, 9229, 27, 40...   
3800  [436, 789, 323, 3081, 1491, 187, 4, 5001, 9451...   
3801  [19252, 28827, 5803, 27279, 4145, 10113, 15691...   
3802  [94, 187, 50262, 61, 2099, 92, 8860, 94, 2490,...   
3803  [1019, 8402, 94, 187, 50262, 61, 2099, 92, 879...   
3804  [43518, 66, 1619, 66, 43518, 66, 1619, 66, 435...   
3805  [60, 18, 62, 608, 187, 50274, 60, 18, 62, 721,...   
3806  [43518, 66, 1619, 66, 43518, 66, 1619, 66, 435...   
3807  [62, 426, 313, 6586, 8880, 5279, 19052, 10, 48...   
3808  [61, 19104, 61, 565, 1559, 61, 7836, 18, 61, 7...   
3809  [92, 8860, 94, 2490, 50262, 61, 2099, 92, 8834...   
3810  [78, 64, 4241, 29834, 17466, 27, 470, 187, 502...   
3811  [1019, 8402, 94, 187, 50262, 61, 2099, 92, 879...   
3812  [50276, 12231, 15, 2490, 50276, 14711, 15, 249...   
3813  [50262, 61, 2099, 92, 8844, 94, 187, 50262, 61...   
3814  [50262, 61, 2099, 92, 8844, 94, 187, 50262, 61...   
3815  [66, 31, 187, 29, 2154, 966, 568, 19259, 14749...   
3816  [26649, 15, 9016, 3, 774, 568, 23745, 3, 1511,...   
3817  [32833, 13, 34915, 4145, 35497, 13, 34984, 107...   
3818  [94, 187, 50262, 61, 2099, 92, 8860, 94, 2490,...   
3819  [5062, 5062, 5062, 5062, 5062, 5062, 5062, 506...   
3820  [7010, 423, 92, 3306, 724, 285, 669, 8604, 60,...   
3821  [9, 9006, 64, 1042, 2025, 13, 322, 9466, 64, 3...   
3822  [187, 50271, 23580, 50270, 740, 187, 50271, 28...   
3823  [15, 17, 313, 783, 346, 17736, 3287, 187, 475,...   
3824  [2490, 50276, 28873, 15, 2490, 50276, 26906, 1...   
3825  [18, 2730, 2551, 31, 42, 36996, 308, 2277, 119...   
3826 

### Classify Subset

### Embedding similarity

In [171]:
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
# Load pre-trained sentence transformer model
embed_model = SentenceTransformer('all-mpnet-base-v2')

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [172]:
pile_embeddings = embed_model.encode(pile_df['text'].str.slice(0,64).to_list(),batch_size=64)

In [173]:
embeddings =embed_model.encode(df_perfect['decoded_full'].to_list(),batch_size=64)


In [174]:
## Just argmax
# sim_matrix = cosine_similarity(embeddings,pile_embeddings)
# # Get the index of the most similar document for each query
# most_similar_idx = sim_matrix.argmax(axis=1)
# # Get the pile_set_name for the most similar documents
# most_similar_pile_sets = pile_df.iloc[most_similar_idx]['pile_set_name']
# # Return array of similarity scores for most similar documents
# max_similarities = sim_matrix.max(axis=1)

## Use KNeighborsClassifier instead of just taking argmax
from sklearn.neighbors import KNeighborsClassifier

# Fit KNN classifier on pile embeddings
knn = KNeighborsClassifier(n_neighbors=10,metric="cosine")
knn.fit(pile_embeddings, pile_df['pile_set_name'])

# Get predictions and distances for each query embedding
distances, _ = knn.kneighbors(embeddings)
most_similar_pile_sets = knn.predict(embeddings)
max_similarites = 1 - distances

In [ ]:
df_perfect['most_similar_pile_set'] = most_similar_pile_sets

In [179]:
df_perfect.head(32)
# df_perfect['max_similarity'] = max_similarites

acc                                            context  \
3795  1.0  [5584, 4196, 1228, 187, 1036, 4, 209, 21723, 2...   
3796  1.0  [50262, 61, 2099, 92, 8861, 94, 187, 50262, 61...   
3797  1.0  [475, 50272, 953, 24781, 778, 320, 908, 281, 1...   
3798  1.0  [424, 380, 16101, 313, 433, 17889, 3104, 10, 2...   
3799  1.0  [3498, 2262, 2369, 40, 736, 13, 3956, 27, 21, ...   
3800  1.0  [187, 187, 4, 21737, 281, 253, 14325, 9107, 68...   
3801  1.0  [66, 15, 3122, 187, 475, 8283, 313, 68, 10, 88...   
3802  1.0  [8161, 13, 2975, 15, 10701, 285, 3915, 9308, 3...   
3803  1.0  [94, 187, 50262, 61, 2043, 92, 3306, 2138, 138...   
3804  1.0  [43518, 66, 1619, 66, 43518, 66, 1619, 66, 435...   
3805  1.0  [187, 50274, 60, 18, 62, 470, 187, 50274, 60, ...   
3806  1.0  [43518, 66, 1619, 66, 43518, 66, 1619, 66, 435...   
3807  1.0  [1010, 558, 187, 50270, 8428, 3145, 60, 1010, ...   
3808  1.0  [1314, 11294, 285, 4974, 32314, 7855, 32705, 6...   
3809  1.0  [3306, 724, 34, 1035, 1637, 47562, 423, 92, 33...   
3810  1.0  [18030, 17466, 27, 470, 187, 50276, 78, 64, 25...   
3811  1.0  [35, 14024, 2407, 92, 86, 16052, 2690, 92, 76,...   
3812  1.0  [50276, 12852, 15, 2490, 50276, 7749, 15, 2490...   
3813  1.0  [1019, 8402, 94, 187, 50262, 61, 2099, 92, 879...   
3814  1.0  [1019, 8402, 94, 187, 50262, 61, 2099, 92, 879...   
3815  1.0  [6877, 36694, 3481, 378, 31219, 2277, 49412, 3...   
3816  1.0  [6740, 568, 19203, 15, 4305, 6750, 3866, 31, 1...   
3817  1.0  [17260, 15, 2949, 7651, 30609, 32221, 3003, 18...   
3818  1.0  [94, 187, 50262, 61, 2043, 92, 3306, 2138, 79,...   
3819  1.0  [625, 35922, 685, 368, 871, 752, 281, 513, 342...   
3820  1.0  [61, 2099, 92, 8828, 94, 187, 50262, 61, 2099,...   
3821  1.0  [50274, 565, 11061, 64, 1088, 28, 535, 50274, ...   
3822  1.0  [50270, 740, 187, 50271, 22000, 50270, 740, 18...   
3823  1.0  [29520, 35491, 1677, 4454, 187, 1413, 27, 4316...   
3824  1.0  [2490, 50276, 32942, 15, 2490, 50276, 32296, 1...   
3825  1.0  [73, 18, 2730, 1288, 31, 2379, 50276, 29, 73, ...   
3826  1.0  [966, 568, 34856, 66, 19, 3, 2654, 568, 26919,...   

                                             generation  \
3795  [783, 346, 17736, 3287, 187, 4, 368, 778, 417,...   
3796  [669, 8604, 60, 805, 431, 1019, 8402, 94, 187,...   
3797  [4110, 33278, 9149, 3003, 28827, 43227, 4889, ...   
3798  [50262, 61, 2099, 92, 8860, 94, 2490, 50262, 6...   
3799  [69, 7675, 27, 2369, 40, 736, 13, 9229, 27, 40...   
3800  [436, 789, 323, 3081, 1491, 187, 4, 5001, 9451...   
3801  [19252, 28827, 5803, 27279, 4145, 10113, 15691...   
3802  [94, 187, 50262, 61, 2099, 92, 8860, 94, 2490,...   
3803  [1019, 8402, 94, 187, 50262, 61, 2099, 92, 879...   
3804  [43518, 66, 1619, 66, 43518, 66, 1619, 66, 435...   
3805  [60, 18, 62, 608, 187, 50274, 60, 18, 62, 721,...   
3806  [43518, 66, 1619, 66, 43518, 66, 1619, 66, 435...   
3807  [62, 426, 313, 6586, 8880, 5279, 19052, 10, 48...   
3808  [61, 19104, 61, 565, 1559, 61, 7836, 18, 61, 7...   
3809  [92, 8860, 94, 2490, 50262, 61, 2099, 92, 8834...   
3810  [78, 64, 4241, 29834, 17466, 27, 470, 187, 502...   
3811  [1019, 8402, 94, 187, 50262, 61, 2099, 92, 879...   
3812  [50276, 12231, 15, 2490, 50276, 14711, 15, 249...   
3813  [50262, 61, 2099, 92, 8844, 94, 187, 50262, 61...   
3814  [50262, 61, 2099, 92, 8844, 94, 187, 50262, 61...   
3815  [66, 31, 187, 29, 2154, 966, 568, 19259, 14749...   
3816  [26649, 15, 9016, 3, 774, 568, 23745, 3, 1511,...   
3817  [32833, 13, 34915, 4145, 35497, 13, 34984, 107...   
3818  [94, 187, 50262, 61, 2099, 92, 8860, 94, 2490,...   
3819  [5062, 5062, 5062, 5062, 5062, 5062, 5062, 506...   
3820  [7010, 423, 92, 3306, 724, 285, 669, 8604, 60,...   
3821  [9, 9006, 64, 1042, 2025, 13, 322, 9466, 64, 3...   
3822  [187, 50271, 23580, 50270, 740, 187, 50271, 28...   
3823  [15, 17, 313, 783, 346, 17736, 3287, 187, 475,...   
3824  [2490, 50276, 28873, 15, 2490, 50276, 26906, 1...   
3825  [18, 2730, 2551, 31, 42, 36996, 308, 2277, 119...   
3826 

In [ ]:
df_perfect

### ChatGPT

In [ ]:
from openai import OpenAI
import pandas as pd
import random

client = OpenAI(api_key=os.getenv("OPENAI_API_KEY"))
def construct_prompt(input_text:str):
    """Build prompt with 2 examples per category from pile_df"""
    examples = []
    
    # Get 2 random examples for each category
    for category in pile_df['pile_set_name'].unique():
        category_examples = pile_df[pile_df['pile_set_name'] == category].sample(2)
        examples.append(f"Category: {category}\nExamples:")
        examples.extend([f"```{text[:64].strip()}```" for text in category_examples['text'].tolist()])
    
    examples_str = "\n\n".join(examples)

    system_prompt = (
        "Classify this text into one of the following Pile Sets based on content and style:\n\n"
        f"{examples_str}\n\n"
        "Answer ONLY with the category name, nothing else."
    )
    prompt = (
        f"Text to classify: ```{input_text.strip()}```\n"        
    )
    return system_prompt, prompt

def classify_text_with_gpt4o(input_text:str):
    """Classify text using GPT-4o-mini with example-based prompting"""
    if not input_text.strip():
        return "Error: Empty input text"
    
    system_prompt, user_prompt = construct_prompt(input_text)    
    
    response = client.chat.completions.create(
        model="gpt-4o",
        messages=[{
            "role": "system",
            "content": system_prompt
        },{
            "role": "user",
            "content": user_prompt
        }],
        temperature=0.1,
        max_tokens=50
    )
    
    return response.choices[0].message.content.strip()

# Example usage
prediction = classify_text_with_gpt4o("Your input text here")
print(f"Predicted category: {prediction}")

Predicted category: Category: Pile-CC


In [20]:
most_similar_pile_sets = df_perfect["decoded_full"].parallel_apply(classify_text_with_gpt4o)

In [28]:
df_perfect['most_similar_pile_set'] = df_perfect['most_similar_pile_set'].apply(lambda x: x.replace("Category:","").strip())

/var/folders/wj/q3w38sf543xc8fy9rx8yqzrh0000gn/T/ipykernel_51977/1092582613.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_perfect['most_similar_pile_set'] = df_perfect['most_similar_pile_set'].apply(lambda x: x.replace("Category:","").strip())


In [29]:
df_perfect['most_similar_pile_set'].value_counts()

most_similar_pile_set
Github                     2437
ArXiv                       843
DM Mathematics              471
Pile-CC                     220
OpenWebText2                181
PubMed Central              129
Books3                      110
FreeLaw                     108
OpenSubtitles               102
StackExchange               100
PubMed Abstracts             72
Wikipedia (en)               65
Gutenberg (PG-19)            35
Ubuntu IRC                   34
BookCorpus2                  26
HackerNews                   22
Error: Empty input text      15
USPTO Backgrounds            15
Enron Emails                  9
NIH ExPorter                  4
PhilPapers                    3
YoutubeSubtitles              2
None                          2
EuroParl                      1
Unknown                       1
Name: count, dtype: int64

In [25]:
df_perfect.to_json("data/mem/perfect_memorization_labeled.jsonl",lines=True,orient="records")

In [87]:
# print("\n".join(f"<row_{i}>\n{v}" for i,v in zip(mem_sample.index,mem_sample.values)))

### Look for corrupted sequences/wrong answers


In [196]:
model = GPTNeoXForCausalLM.from_pretrained(MODEL_NAME)
model = model.to(device)

In [197]:
toks = tokenizer("When Mary and John went to the store, John gave a drink to",return_tensors="pt")["input_ids"]
toks = toks.to(device)
logits = model(toks)


In [207]:
toks.size()

torch.Size([1, 14])

In [209]:
tokenizer.decode(logits.logits.argmax(dim=-1)[:,-1])

' the'

In [204]:
tokenizer.decode(logits.logits.argmax(dim=-1)[0])

' the was I were to the house to she and them small to the'

In [84]:
context =t.tensor(df_perfect["context"].to_list())
generation = t.tensor(df_perfect["generation"].to_list())

In [85]:
# Move model to device and set to eval mode
model = model.to(device)
model.eval()

# Process in batches to avoid memory issues
batch_size = 32
outputs = []

with t.no_grad():
    for i in range(0, len(context), batch_size):
        batch = context[i:i + batch_size].to(device)
        # Get model outputs including all logits

        batch_output = model.generate(batch, max_new_tokens=32, return_dict_in_generate=True, output_logits=True, output_attentions=True)        
        break

# Concatenate all batches
# all_outputs = t.cat(outputs, dim=0)


The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


### Attention scores

In [35]:
from bertviz import head_view

In [51]:
first_attentions = []
for step in batch_output.attentions[0]:
    first_attentions.append(step[1,...].unsqueeze(0))

In [103]:
sample_attentions = []
for layer_idx in range(len(batch_output.attentions[0])):  # Iterate through layers
    # Initialize tensor for this layer
    layer_attentions = []
    
    # Get attention for first step (full context attention)
    first_step = batch_output.attentions[0][layer_idx]  # [batch_size, num_heads, seq_len, seq_len]
    
    target_size = first_step.size(-1) + len(batch_output.attentions)
    
    padded_first_step = t.nn.functional.pad(
        first_step,
        (0, target_size - first_step.size(-1),  # Pad last dimension
         0, target_size - first_step.size(-2))   # Pad second-to-last dimension
    )
    layer_attentions.append(padded_first_step)
    
    # Add attention from subsequent steps
    for step_idx, step in enumerate(batch_output.attentions[1:], start=1):
        step_attn = step[layer_idx]  # [batch_size, num_heads, 1, seq_len+step]
        # Pad to match target size
        # Create zero tensor of target size
        full_attn = t.zeros(step_attn.shape[0], step_attn.shape[1], target_size, target_size, device=step_attn.device)
        
        # Place the attention scores in the correct row (corresponding to the current token)
        full_attn[:, :, first_step.size(-1) + step_idx - 1, :step_attn.size(-1)] = step_attn.squeeze(2)
        
        layer_attentions.append(full_attn)
    
    # Combine all steps
    combined_attention = t.sum(t.stack(layer_attentions), dim=0) # Sum across steps
    sample_attentions.append(combined_attention)

In [132]:
batch_id = 28

In [133]:
first_attentions = [l[batch_id,...].unsqueeze(0) for l in sample_attentions]
tokens = tokenizer.convert_ids_to_tokens(batch_output.sequences[batch_id])
# first generation tokens


'Spanish feminine given names\nCategory:Scandinavian feminine given names/*\n * Copyright 2018 IBM Corporation\n *\n * Licensed under the Apache License, Version 2'

In [156]:
tokenizer.decode(batch_output.sequences[batch_id][:32]),tokenizer.decode(batch_output.sequences[batch_id][32:])

('Spanish feminine given names\nCategory:Scandinavian feminine given names/*\n * Copyright 2018 IBM Corporation\n *\n * Licensed under the Apache License, Version 2',
 '.0 (the "License");\n * you may not use this file except in compliance with the License.\n * You may obtain a copy of the License')

In [168]:
corrupted_ids = tokenizer(tokenizer.decode(context[batch_id]).replace("given names", "surnames",1),return_tensors="pt")
corrupted_ids = corrupted_ids["input_ids"].to(device)
corrupted_ids.size()

torch.Size([1, 33])

In [150]:
corrupted_output = model.generate(corrupted_ids, max_new_tokens=32, return_dict_in_generate=True, output_logits=True, output_attentions=True)        

The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:None for open-end generation.


In [170]:
tokenizer.decode(corrupted_output.sequences[0][:34]),tokenizer.decode(corrupted_output.sequences[0][34:])

('Spanish feminine given surnames\nCategory:Scandinavian feminine given names/*\n * Copyright 2018 IBM Corporation\n *\n * Licensed under the Apache License, Version 2',
 '.0 (the "License");\n * you may not use this file except in compliance with the License.\n * You may obtain a copy of the License')

In [134]:
head_view(first_attentions,tokens,layer=5)

<IPython.core.display.Javascript object>

In [188]:
# Initialize lists to store results
max_attended_tokens = []
attention_scores = []

# Process each generation step
for step_idx, attn in enumerate(batch_output.attentions):
    # Get last layer attention
    last_layer = attn[-1]  # [batch_size, num_heads, seq_len_q, seq_len_k]
    
    # Aggregate across heads: max or mean

    # agg_attn,_ = last_layer.max(dim=1)
    agg_attn = last_layer.mean(dim=1)  # [batch_size, seq_len_q, seq_len_k]
    
    # Get the token with maximum attention for each query
    max_attn_scores, max_attn_indices = agg_attn.max(dim=-1)  # [batch_size, seq_len_q]
    
    # We only care about the last position (new token)
    max_attended_tokens.append(max_attn_indices[:, -1])  # [batch_size]
    attention_scores.append(max_attn_scores[:, -1])  # [batch_size]

# Convert to tensors
max_attended_tokens = t.stack(max_attended_tokens)  # [num_tokens, batch_size]
attention_scores = t.stack(attention_scores)  # [num_tokens, batch_size]


In [189]:
# Print example for first sequence
print(f"Example attention analysis for sequence # {batch_id}:")
generated_tokens = batch_output.sequences[batch_id]  # Skip context
input_tokens = context[batch_id].tolist()

print(f"Length of input tokens: {len(input_tokens)}")
print(f"Length of generated tokens: {len(generated_tokens)}")
print(f"Shape of max_attended_tokens: {max_attended_tokens.shape}")

for i, gen_token in enumerate(generated_tokens[32:]):
    max_attn_idx = max_attended_tokens[i, 0].item()
    attn_score = attention_scores[i, 0].item()
    
    # Add bounds checking
    if max_attn_idx < len(generated_tokens):
        input_token = tokenizer.convert_ids_to_tokens([generated_tokens[max_attn_idx]])
        gen_token_decoded = tokenizer.convert_ids_to_tokens([gen_token])
        print(f"[{32+i}] Generated token '{gen_token_decoded}' attends most to input token '{input_token}'[{max_attn_idx}] (score: {attn_score:.3f})")
    else:
        print(f"Warning: attention index {max_attn_idx} out of range for input length {len(generated_tokens)}")

Example attention analysis for sequence # 28:
Length of input tokens: 32
Length of generated tokens: 64
Shape of max_attended_tokens: torch.Size([32, 32])
[32] Generated token '['.']' attends most to input token '['Ġnames']'[3] (score: 0.240)
[33] Generated token '['0']' attends most to input token '['.']'[32] (score: 0.257)
[34] Generated token '['Ġ(']' attends most to input token '['.']'[32] (score: 0.277)
[35] Generated token '['the']' attends most to input token '['Ġ(']'[34] (score: 0.337)
[36] Generated token '['Ġ"']' attends most to input token '['Ġnames']'[3] (score: 0.442)
[37] Generated token '['License']' attends most to input token '['Ġnames']'[3] (score: 0.528)
[38] Generated token '['");']' attends most to input token '['the']'[35] (score: 0.750)
[39] Generated token '['Ċ']' attends most to input token '['");']'[38] (score: 0.347)
[40] Generated token '['Ġ*']' attends most to input token '['Ġnames']'[3] (score: 0.334)
[41] Generated token '['Ġyou']' attends most to input t

In [17]:
batch_output.attentions[0][-1].size()

torch.Size([32, 8, 32, 32])

In [12]:
len(batch_output.attentions)

32

In [ ]:
batch_output.sequences[0,32:] == generation[0]

tensor([  783,   346, 17736,  3287,   187,     4,   368,   778,   417,   897,
          436,  1873,  3707,   275, 10276,   342,   253,  4637,    15,   187,
            4,  1422,   778,  4044,   247,  3491,   273,   253,  4637,   387,
          187,     4], device='mps:0')

In [61]:
top_tokens = []
top_probs = []
for gen_logits in batch_output.logits:
    gen_logits = t.softmax(gen_logits,dim=-1)
    topk = gen_logits.topk(k=5,dim=-1)
    top_tokens.append(topk[1].unsqueeze(1)) # [batch_size, 1, 5]
    top_probs.append(topk[0].unsqueeze(1)) # [batch_size, 1, 5]
top_tokens = t.cat(top_tokens,dim=1) # [batch_size, max_new_tokens, 5]
top_probs = t.cat(top_probs,dim=1) # [batch_size, max_new_tokens, 5]

### Explore dataset

In [10]:
tokenizer = AutoTokenizer.from_pretrained(MODEL_NAME)

In [11]:
sample = df_perfect.sample(5)
print("Sample of perfectly memorized sequences:")
for i,row  in sample.iterrows():    
    print("\nExample", i)
    print("Context:", tokenizer.decode(row['context']))
    print("True continuation:", tokenizer.decode(row['true_continuation']))

Sample of perfectly memorized sequences:

Example 19936
Context: /licenses/CDDL+GPL-1.1
# or LICENSE.txt.  See the License for the specific
# language governing permissions and limitations
True continuation:  under the License.
#
# When distributing the software, include this License Header Notice in each
# file and include the License file at LICENSE.txt

Example 4152
Context: {D})$\end{document}$, $\documentclass[12pt]{minimal}
                \usepackage{amsmath}
                \usepackage{wasysym} 
                
True continuation: \usepackage{amsfonts} 
                \usepackage{amssymb} 
                \usepackage{amsbsy}
                \usepackage{mathrsfs}
                \usepackage{upgreek

Example 9532
Context: [12pt]{minimal}
                \usepackage{amsmath}
                \usepackage{wasysym} 
                \usepackage{amsfonts} 
                \usepackage{
True continuation: amssymb} 
                \usepackage{amsbsy}
                \usepackage{mathrsfs}

In [13]:
import filter.pattern_filter as pattern_filter
import importlib
importlib.reload(pattern_filter)
def is_simple_pattern(x):
    tokens = tokenizer.decode(x["context"])
    continuation = tokenizer.decode(x["true_continuation"]) 
    return pattern_filter.is_simple_pattern(tokens,continuation)
df_perfect['to_filter'] = df_perfect.apply(is_simple_pattern,axis=1)
# mem_sample = df_perfect[df_perfect['most_similar_pile_set'] == "Wikipedia (en)"]
# text = ""
# for i,row in mem_sample.iterrows():
#     tokens = tokenizer.decode(row['context'])
#     continuation = tokenizer.decode(row['true_continuation'])
#     text += f"<row_{i}>\n{tokens}\n<completion>{continuation}\n</row_{i}>\n"
# print(text)

/var/folders/wj/q3w38sf543xc8fy9rx8yqzrh0000gn/T/ipykernel_38880/377531716.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_perfect['to_filter'] = df_perfect.apply(is_simple_pattern,axis=1)


In [14]:
ids = [3823,  4213,  4462,  4490,  4565,  4599,  9001,  9068,  9503,  9724,  9844,  9856,  9906,  14050,  14166,  14371,  14533,  14537,  19050,  19439,  19603,  19858,  19891,  20000]
samples = df_perfect[df_perfect.index.isin(ids)]

In [15]:
samples

acc                                            context  \
3823   1.0  [29520, 35491, 1677, 4454, 187, 1413, 27, 4316...   
4213   1.0  [13, 253, 5304, 540, 251, 1050, 16417, 275, 86...   
4462   1.0  [1688, 313, 6448, 898, 4437, 24652, 10, 310, 2...   
4490   1.0  [44926, 209, 15765, 6781, 187, 187, 29, 34, 34...   
4565   1.0  [13, 11432, 6884, 27141, 13, 36481, 13, 253, 4...   
4599   1.0  [31, 187, 870, 2851, 31, 187, 870, 1206, 31, 1...   
9001   1.0  [7, 6732, 45599, 7, 6732, 13143, 965, 31, 187,...   
9068   1.0  [4437, 25124, 10, 310, 247, 19701, 45125, 505,...   
9503   1.0  [733, 310, 1119, 327, 6984, 356, 4843, 274, 15...   
9724   1.0  [6491, 13, 12412, 5720, 13, 44, 300, 76, 10614...   
9844   1.0  [642, 3332, 1543, 323, 4633, 20503, 7774, 15, ...   
9856   1.0  [8056, 656, 11094, 2956, 6419, 30952, 32735, 1...   
9906   1.0  [17, 3, 411, 24282, 568, 2313, 28764, 7956, 22...   
14050  1.0  [45599, 7, 6732, 13143, 965, 31, 187, 29, 965,...   
14166  1.0  [1413, 27, 42531, 2892, 273, 40115, 571, 14340...   
14371  1.0  [9643, 10, 3706, 15946, 13, 7252, 253, 34806, ...   
14533  1.0  [1413, 27, 14619, 16258, 187, 1413, 27, 31969,...   
14537  1.0  [10694, 14, 1525, 43189, 2383, 32559, 1570, 18...   
19050  1.0  [6629, 275, 5002, 187, 1413, 27, 15491, 29345,...   
19439  1.0  [7796, 13, 5266, 15, 187, 187, 42, 574, 271, 2...   
19603  1.0  [16372, 1279, 17363, 13, 534, 1462, 323, 253, ...   
19858  1.0  [14, 9888, 546, 12642, 11802, 6358, 187, 1413,...   
19891  1.0  [327, 253, 6105, 1580, 352, 369, 6312, 275, 25...   
20000  1.0  [22696, 275, 5427, 187, 1413, 27, 2447, 953, 2...   

                                              generation  \
3823   [15, 17, 313, 783, 346, 17736, 3287, 187, 475,...   
4213   [310, 634, 806, 4143, 13, 320, 2119, 281, 187,...   
4462   [187, 1413, 27, 41083, 10782, 187, 1413, 27, 1...   
4490   [7956, 2293, 49, 19873, 2637, 568, 20, 3, 7956...   
4565   [10850, 13, 285, 253, 4454, 13, 15278, 7886, 1...   
4599   [335, 966, 568, 29589, 1138, 187, 29, 965, 966...   
9001   [1138, 6942, 870, 66, 3073, 965, 31, 187, 870,...   
9068   [14316, 952, 187, 1413, 27, 7638, 763, 5086, 2...   
9503   [16169, 187, 4, 187, 4, 21737, 762, 253, 14325...   
9724   [285, 697, 2330, 11547, 403, 2120, 15299, 2758...   
9844   [490, 6992, 3390, 253, 7185, 273, 6519, 13, 39...   
9856   [15, 2061, 16, 3125, 16, 2974, 21, 16, 4213, 5...   
9906   [21849, 4350, 1539, 30, 19, 49249, 10817, 4891...   
14050  [870, 66, 3073, 965, 31, 187, 870, 335, 31, 18...   
14166  [17, 68, 2320, 14, 2504, 3156, 14, 4185, 1348,...   
14371  [253, 3745, 281, 26542, 3806, 12028, 285, 7774...   
14533  [14154, 2715, 18133, 3821, 1458, 4765, 884, 27...   
14537  [793, 15, 14111, 15, 11340, 9, 3701, 6734, 551...   
19050  [11099, 374, 15, 17, 313, 783, 346, 17736, 328...   
19439  [9596, 13, 390, 43987, 253, 1959, 5763, 10445,...   
19603  [13, 253, 84, 32091, 13, 6239, 13, 37756, 13, ...   
19858  [373, 16, 9152, 3, 187, 50274, 9152, 27, 3429,...   
19891  [27, 475, 1348, 1797, 475, 37396, 577, 17913, ...   
20000  [605, 1400, 3, 346, 2413, 1358, 2700, 15, 88, ...   

                                       true_continuation        idx  \
3823   [15, 17, 313, 783, 346, 17736, 3287, 187, 475,...      14556   
4213   [310, 634, 806, 4143, 13, 320, 2119, 281, 187,...     144066   
4462   [187, 1413, 27, 41083, 10782, 187, 1413, 27, 1...     235037   
4490   [7956, 2293, 49, 19873, 2637, 568, 20, 3, 7956...     244375   
4565   [10850, 13, 285, 253, 4454, 13, 15278, 7886, 1...     269366   
4599   [335, 966, 568, 29589, 1138, 187, 29, 965, 966...     278199   
9001   [1138, 6942, 870, 66, 3073, 965, 31, 187, 870,...   36666858   
9068   [14316, 952, 187, 1413, 27, 7638, 763, 5086, 2...   36685465   
9503   [16169, 187, 4, 187, 4, 21737, 762, 253, 14325...   36838589   
9724   [285, 697, 2330, 11547, 403, 2120, 15299, 2758...   36917139   
9844   [490, 6992, 3390, 253, 7185, 273, 6519, 13, 39...   36956090   
9856   [15, 2061, 16, 3125, 

## Attention Heads Activation Frequency

In [19]:
import json
with open("data/mem/contexts.jsonl","w") as f:
    for c in samples.apply(lambda x: tokenizer.decode(x["context"]),axis=1).values:
        f.write(json.dumps(c) + "\n")
with open("data/mem/completions.jsonl","w") as f:
    for c in samples.apply(lambda x: tokenizer.decode(x["true_continuation"]),axis=1).values:
        f.write(json.dumps(c) + "\n")

In [15]:
import json
general_samples =df[df['acc'] == 0]

with open("data/mem/contexts_0mem.jsonl","w") as f:
    for c in general_samples.apply(lambda x: tokenizer.decode(x["context"]),axis=1).values:
        f.write(json.dumps(c) + "\n")
with open("data/mem/completions_gen_0mem.jsonl","w") as f:
    for c in general_samples.apply(lambda x: tokenizer.decode(x["generation"]),axis=1).values:
        f.write(json.dumps(c) + "\n")
with open("data/mem/completions_true_0mem.jsonl","w") as f:
    for c in general_samples.apply(lambda x: tokenizer.decode(x["true_continuation"]),axis=1).values:
        f.write(json.dumps(c) + "\n")

## Find circuits

In [8]:
import torch as t
from auto_circuit.data import PromptDataLoader, PromptDataset
from torch.utils.data import Subset


In [9]:
def to_autocircuit_ds(df:pd.DataFrame,return_seq_length: bool = False,tail_divergence: bool = False, test_size: float = 0.1, batch_size: int | tuple[int, int] = 8):

    # Convert all columns to tensors
    context = t.tensor(df["context"].to_list())
    true_continuation = t.tensor(df["true_continuation"].to_list())
    generation = t.tensor(df["generation"].to_list())

    
    dataset = PromptDataset(clean_prompts=context.to(device), 
                            corrupt_prompts=context.to(device),  # TODO: think about how to corrupt
                            answers=[a[0].unsqueeze(0).to(device) for a in generation], # Take first token of continuation
                            wrong_answers=[a[0].unsqueeze(0).to(device) for a in generation],)   # TODO: why generation is wrong?
     
    dataset_size = len(dataset)
    train_size = int(dataset_size * (1 - test_size))
    train_set = Subset(dataset, list(range(train_size)))
    test_set = Subset(dataset, list(range(train_size, dataset_size)))

    seq_len = None    
    diverge_idx: int = 0
    kvs = []
    if return_seq_length:        
        seq_len = df["context"].shape[1]
    
    if tail_divergence:
        diverge_idxs = (~(df["context"] == df["context"])).int().argmax(dim=1)
        diverge_idx = int(diverge_idxs.min().item())
    if diverge_idx > 0:
        raise NotImplementedError()

    train_loader = PromptDataLoader(
        train_set,
        seq_len=seq_len,
        diverge_idx=diverge_idx,
        kv_cache=kvs[0] if len(kvs) > 0 else None,
        seq_labels=None,
        word_idxs=None,
        batch_size=batch_size[0] if isinstance(batch_size, tuple) else batch_size,
        shuffle=False,
    )
    test_loader = PromptDataLoader(
        test_set,
        seq_len=seq_len,
        diverge_idx=diverge_idx,
        kv_cache=kvs[-1] if len(kvs) > 0 else None,
        seq_labels=None,
        word_idxs=None,
        batch_size=batch_size[1] if isinstance(batch_size, tuple) else batch_size,
        shuffle=False,
    )
    return train_loader, test_loader


In [10]:
train_loader, test_loader = to_autocircuit_ds(df_perfect)

/var/folders/wj/q3w38sf543xc8fy9rx8yqzrh0000gn/T/ipykernel_23338/2539828788.py:4: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at /Users/runner/work/pytorch/pytorch/pytorch/torch/csrc/utils/tensor_new.cpp:281.)
  context = t.tensor(df["context"].to_list())


In [11]:
len(train_loader)

563

In [41]:
from auto_circuit.experiment_utils import load_tl_model
from auto_circuit.types import AblationType, PatchType, PruneScores
from auto_circuit.utils.graph_utils import patchable_model,edge_counts_util

from auto_circuit.utils.tensor_ops import prune_scores_threshold
from auto_circuit.prune_algos.mask_gradient import mask_gradient_prune_scores
from auto_circuit.prune import run_circuits
from auto_circuit.metrics.prune_metrics.kl_div import measure_kl_div
from auto_circuit.metrics.prune_metrics.answer_diff import measure_answer_diff
from auto_circuit.metrics.prune_metrics.answer_value import measure_answer_val,batch_avg_answer_val
from auto_circuit.visualize import draw_seq_graph

def find_circuits(model,
                  train_loader:PromptDataLoader, 
                  test_loader:PromptDataLoader,
                  ablation_type=AblationType.RESAMPLE,
                  patch_type=PatchType.TREE_PATCH):

    prune_scores: PruneScores = mask_gradient_prune_scores(
        model=model,
        dataloader=train_loader,
        official_edges=None,
        grad_function="logit",
        answer_function="avg_diff",
        mask_val=0.0, 
        ablation_type=ablation_type
    )
    edge_count = edge_counts_util(model.edges, prune_scores=prune_scores)

    return prune_scores, run_circuits(model,test_loader,edge_count,prune_scores,ablation_type=ablation_type,patch_type=patch_type)

def find_min_circuit(circuit_accuracy,base_accuracy,eps:float=0.2):
    model_edge_count, base_acc = base_accuracy[0]
    for edge_count, acc in circuit_accuracy:
        if acc and (abs(acc - base_acc) / base_acc) < eps:
            return edge_count, acc
    return model_edge_count, base_acc

In [13]:
tl_model = load_tl_model(MODEL_NAME, device)
p_model = patchable_model(
    tl_model,
    factorized=True,
    slice_output="last_seq",
    separate_qkv=True,
    device=device,
    ignore_tokens=[]
)

Loaded pretrained model EleutherAI/pythia-70m-deduped into HookedTransformer


In [14]:
path = Path(f"{MODEL_NAME.split('/')[-1]}_mem_prune_scores.pkl")
if path.exists():
    prune_scores: PruneScores = t.load(path)
else:
    prune_scores: PruneScores = mask_gradient_prune_scores(
        model=p_model,
        dataloader=train_loader,
        official_edges=None,
        grad_function="logit",
        answer_function="avg_val",
        mask_val=0.0, 
        ablation_type=AblationType.ZERO
    )

/var/folders/wj/q3w38sf543xc8fy9rx8yqzrh0000gn/T/ipykernel_23338/3825750624.py:3: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  prune_scores: PruneScores = t.load(path)


In [16]:
edge_count = edge_counts_util(p_model.edges, prune_scores=prune_scores)
outs = run_circuits(p_model,test_loader,edge_count,prune_scores,ablation_type=AblationType.ZERO,patch_type=PatchType.TREE_PATCH)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [42]:
threshold = prune_scores_threshold(prune_scores, 100)
threshold

tensor(290.5211, device='mps:0')

In [43]:
fig = draw_seq_graph(
    p_model, prune_scores, threshold.item(), layer_spacing=True, orientation="v"
)

In [34]:
outs.keys()

dict_keys([0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 20, 30, 40, 50, 60, 70, 80, 90, 100, 200, 300, 400, 500, 600, 700, 800, 900, 1000, 2000, 3000, 3580])

In [44]:
first100 = {k:v for k,v in outs.items() if k <= 100}

In [45]:
val_results = measure_answer_val(p_model,test_loader,first100)

In [46]:
val_results

[(0, 12.57073974609375),
 (1, 12.57073974609375),
 (2, 11.126285552978516),
 (3, 12.338752746582031),
 (4, 12.338752746582031),
 (5, 11.980280876159668),
 (6, 11.901838302612305),
 (7, 10.829748153686523),
 (8, 10.829748153686523),
 (9, 9.464014053344727),
 (10, 9.464014053344727),
 (20, 9.890220642089844),
 (30, 10.33684253692627),
 (40, 7.953545093536377),
 (50, 7.934033393859863),
 (60, 7.9774088859558105),
 (70, 8.016780853271484),
 (80, 8.02933406829834),
 (90, 8.076476097106934),
 (100, 8.047252655029297)]

In [20]:
kl_results = measure_kl_div(p_model,test_loader,outs)

KeyboardInterrupt: 

In [42]:
prune_scores_base, circuits_out_base = find_circuits(p_model,train_loader,test_loader)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


: 

In [ ]:

# base_accuracy = measure_correct_ans_percent_model(p_model,test_loader)
# circuit_accuracy_base = measure_correct_ans_percent(p_model,test_loader,circuits_out_base)
best_edge_count,best_circuit_accuracy = find_min_circuit(circuit_accuracy_base,base_accuracy)
threshold_base = prune_scores_threshold(prune_scores_base, best_edge_count).detach().item()